# Imports

In [11]:
#!pip install catboost

In [12]:
import pandas as pd
import numpy as np

from sklearn.ensemble import RandomForestRegressor
from sklearn.preprocessing import RobustScaler, StandardScaler
from sklearn.preprocessing import OneHotEncoder, OrdinalEncoder
from sklearn.model_selection import train_test_split
from sklearn.linear_model import LogisticRegression
from sklearn.metrics import roc_auc_score
from sklearn.metrics import mean_squared_error
import catboost as cb

# Read diamonds

In [13]:
diamonds_train_sorted = pd.read_csv('../data/diamonds_train_sorted.csv')
diamonds_train_sorted.head()

price  carat  cut  color  clarity  depth  table     x     y     z
0    326   0.21    4      1        2   59.8   61.0  3.89  3.84  2.31
1    326   0.23    0      1        1   61.5   55.0  3.95  3.98  2.43
2    327   0.23    1      1        4   56.9   65.0  4.05  4.07  2.31
3    334   0.29    4      5        3   62.4   58.0  4.20  4.23  2.63
4    335   0.31    1      6        1   63.3   58.0  4.34  4.35  2.75

# Feature engineering

In [51]:
diamonds_train_sorted['table_xy'] = (diamonds_train_sorted['table'].mean()*(diamonds_train_sorted['x']*diamonds_train_sorted['y']).mean()-diamonds_train_sorted['table']*(diamonds_train_sorted['x']*diamonds_train_sorted['y']))
diamonds_train_sorted['depth_z'] = (diamonds_train_sorted['depth'].mean()*diamonds_train_sorted['z'].mean()-diamonds_train_sorted['depth']*diamonds_train_sorted['z'])
diamonds_train_sorted['volume'] = diamonds_train_sorted['x']*diamonds_train_sorted['y']*diamonds_train_sorted['z']
diamonds_train_sorted['super_feature'] = diamonds_train_sorted['carat'] / diamonds_train_sorted['table'] * diamonds_train_sorted['depth']
diamonds_train_sorted.head()

price  carat  cut  color  clarity  depth  table     x     y     z  \
0    326   0.21    4      1        2   59.8   61.0  3.89  3.84  2.31   
1    326   0.23    0      1        1   61.5   55.0  3.95  3.98  2.43   
2    327   0.23    1      1        4   56.9   65.0  4.05  4.07  2.31   
3    334   0.29    4      5        3   62.4   58.0  4.20  4.23  2.63   
4    335   0.31    1      6        1   63.3   58.0  4.34  4.35  2.75   

      table_xy    depth_z     volume  super_feature  
0  1047.776468  80.291287  34.505856       0.205869  
1  1094.315068  68.984287  38.202030       0.257182  
2   887.542568  86.990287  38.076885       0.201338  
3   928.542068  54.317287  46.724580       0.312000  
4   863.988068  44.354287  51.917250       0.338328

# Model train split

In [53]:
X = diamonds_train_sorted[['carat', 
                           'cut',
                           'color', 
                           'clarity',
                           'table_xy', 
                           'depth_z',
                          'volume',
                          'super_feature']]

y = diamonds_train_sorted['price']

In [54]:
# Train + test
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size = 0.2, random_state = 42)
print(f"X_train: {X_train.shape}, X_test: {X_test.shape}, y_train: {y_train.shape}, y_test: {y_test.shape}")
print(f"X_train: {type(X_train)}, X_test: {type(X_test)}, y_train: {type(y_train)}, y_test: {type(y_test)}")

X_train: (32364, 8), X_test: (8091, 8), y_train: (32364,), y_test: (8091,)
X_train: <class 'pandas.core.frame.DataFrame'>, X_test: <class 'pandas.core.frame.DataFrame'>, y_train: <class 'pandas.core.series.Series'>, y_test: <class 'pandas.core.series.Series'>


# Train model CatBoost

In [55]:
# rf model train
train_dataset = cb.Pool(X_train, y_train) 
test_dataset = cb.Pool(X_test, y_test)

In [56]:
model = cb.CatBoostRegressor(loss_function='RMSE')

In [57]:
grid = {'iterations': [100, 150, 500],
        'learning_rate': [0.03, 0.1, 0.3],
        'depth': [2, 4, 6, 8],
        'l2_leaf_reg': [0.2, 0.5, 1, 3]}
model.grid_search(grid, train_dataset)

0:	learn: 5442.3566522	test: 5440.4017694	best: 5440.4017694 (0)	total: 2.99ms	remaining: 296ms
1:	learn: 5298.8803055	test: 5295.7213150	best: 5295.7213150 (1)	total: 5.64ms	remaining: 276ms
2:	learn: 5161.6334455	test: 5158.1817025	best: 5158.1817025 (2)	total: 7.87ms	remaining: 255ms
3:	learn: 5030.9850182	test: 5028.8057984	best: 5028.8057984 (3)	total: 10.5ms	remaining: 251ms
4:	learn: 4900.0110786	test: 4897.0996998	best: 4897.0996998 (4)	total: 12.7ms	remaining: 241ms
5:	learn: 4773.6606728	test: 4770.7774484	best: 4770.7774484 (5)	total: 14.9ms	remaining: 234ms
6:	learn: 4651.6533553	test: 4647.8453168	best: 4647.8453168 (6)	total: 17.1ms	remaining: 227ms
7:	learn: 4534.8559034	test: 4532.2518865	best: 4532.2518865 (7)	total: 19.4ms	remaining: 223ms
8:	learn: 4419.6999968	test: 4416.6761121	best: 4416.6761121 (8)	total: 21.5ms	remaining: 217ms
9:	learn: 4308.3342231	test: 4304.6600122	best: 4304.6600122 (9)	total: 23.6ms	remaining: 213ms
10:	learn: 4201.1850484	test: 4196.65653

93:	learn: 1372.9257231	test: 1397.2614550	best: 1397.2614550 (93)	total: 204ms	remaining: 13ms
94:	learn: 1366.9390395	test: 1391.8731143	best: 1391.8731143 (94)	total: 207ms	remaining: 10.9ms
95:	learn: 1359.0456303	test: 1384.1959642	best: 1384.1959642 (95)	total: 209ms	remaining: 8.7ms
96:	learn: 1350.9529934	test: 1376.0035019	best: 1376.0035019 (96)	total: 212ms	remaining: 6.55ms
97:	learn: 1344.8309742	test: 1370.2722476	best: 1370.2722476 (97)	total: 214ms	remaining: 4.37ms
98:	learn: 1337.9085764	test: 1363.2461503	best: 1363.2461503 (98)	total: 217ms	remaining: 2.19ms
99:	learn: 1331.7687798	test: 1357.2609774	best: 1357.2609774 (99)	total: 221ms	remaining: 0us

bestTest = 1357.260977
bestIteration = 99

0:	loss: 1357.2609774	best: 1357.2609774 (0)	total: 268ms	remaining: 38.3s
0:	learn: 5094.9666380	test: 5090.4054223	best: 5090.4054223 (0)	total: 4.19ms	remaining: 415ms
1:	learn: 4656.2596810	test: 4648.1256266	best: 4648.1256266 (1)	total: 6.97ms	remaining: 341ms
2:	learn:

55:	learn: 775.3838637	test: 808.5322250	best: 808.5322250 (55)	total: 119ms	remaining: 93.4ms
56:	learn: 774.2722337	test: 807.6415873	best: 807.6415873 (56)	total: 121ms	remaining: 91.5ms
57:	learn: 771.8318140	test: 805.2731075	best: 805.2731075 (57)	total: 123ms	remaining: 89.3ms
58:	learn: 769.8675135	test: 803.4653145	best: 803.4653145 (58)	total: 126ms	remaining: 87.4ms
59:	learn: 766.5580527	test: 799.6169202	best: 799.6169202 (59)	total: 128ms	remaining: 85.2ms
60:	learn: 765.4443689	test: 798.6117197	best: 798.6117197 (60)	total: 130ms	remaining: 83.2ms
61:	learn: 762.7764198	test: 795.1612290	best: 795.1612290 (61)	total: 132ms	remaining: 81.1ms
62:	learn: 760.4269753	test: 792.0933823	best: 792.0933823 (62)	total: 134ms	remaining: 78.9ms
63:	learn: 758.8990399	test: 791.0055984	best: 791.0055984 (63)	total: 137ms	remaining: 76.8ms
64:	learn: 758.4372885	test: 790.8400728	best: 790.8400728 (64)	total: 139ms	remaining: 74.9ms
65:	learn: 755.7379081	test: 787.6863874	best: 787

4:	learn: 3618.5244783	test: 3617.5114362	best: 3617.5114362 (4)	total: 15.7ms	remaining: 299ms
5:	learn: 3342.0928514	test: 3342.9845017	best: 3342.9845017 (5)	total: 18.1ms	remaining: 284ms
6:	learn: 3092.1948973	test: 3090.6422651	best: 3090.6422651 (6)	total: 20.5ms	remaining: 273ms
7:	learn: 2872.7196969	test: 2873.7383668	best: 2873.7383668 (7)	total: 22.8ms	remaining: 262ms
8:	learn: 2680.8482852	test: 2681.8982988	best: 2681.8982988 (8)	total: 25.1ms	remaining: 254ms
9:	learn: 2509.1090459	test: 2511.5928411	best: 2511.5928411 (9)	total: 27.2ms	remaining: 245ms
10:	learn: 2357.8195328	test: 2360.2720631	best: 2360.2720631 (10)	total: 29.4ms	remaining: 238ms
11:	learn: 2225.9009677	test: 2231.6333927	best: 2231.6333927 (11)	total: 31.5ms	remaining: 231ms
12:	learn: 2112.1995152	test: 2119.4210816	best: 2119.4210816 (12)	total: 33.7ms	remaining: 225ms
13:	learn: 2014.3757113	test: 2022.7184884	best: 2022.7184884 (13)	total: 36.1ms	remaining: 222ms
14:	learn: 1925.5545934	test: 19

67:	learn: 755.2437154	test: 787.9131544	best: 787.9131544 (67)	total: 159ms	remaining: 74.6ms
68:	learn: 751.7022896	test: 784.0081351	best: 784.0081351 (68)	total: 161ms	remaining: 72.3ms
69:	learn: 750.3264675	test: 783.6427942	best: 783.6427942 (69)	total: 163ms	remaining: 70ms
70:	learn: 747.3681953	test: 779.9724598	best: 779.9724598 (70)	total: 165ms	remaining: 67.5ms
71:	learn: 746.4275086	test: 780.4316418	best: 779.9724598 (70)	total: 167ms	remaining: 65.1ms
72:	learn: 744.2709488	test: 778.0201354	best: 778.0201354 (72)	total: 170ms	remaining: 62.7ms
73:	learn: 739.7578332	test: 773.9120949	best: 773.9120949 (73)	total: 172ms	remaining: 60.4ms
74:	learn: 739.0725424	test: 773.3659162	best: 773.3659162 (74)	total: 174ms	remaining: 58ms
75:	learn: 737.8101719	test: 771.9577843	best: 771.9577843 (75)	total: 178ms	remaining: 56.1ms
76:	learn: 737.5021906	test: 771.8785327	best: 771.8785327 (76)	total: 181ms	remaining: 54ms
77:	learn: 735.2486338	test: 769.4733941	best: 769.47339

...

175:	learn: 555.4829297	test: 569.8180892	best: 569.8180892 (175)	total: 1.18s	remaining: 2.18s
176:	learn: 554.8668796	test: 569.3391430	best: 569.3391430 (176)	total: 1.19s	remaining: 2.17s
177:	learn: 554.1594217	test: 569.1899592	best: 569.1899592 (177)	total: 1.2s	remaining: 2.16s
178:	learn: 553.6288186	test: 568.7352780	best: 568.7352780 (178)	total: 1.21s	remaining: 2.16s
179:	learn: 552.9481923	test: 568.2816574	best: 568.2816574 (179)	total: 1.21s	remaining: 2.15s
180:	learn: 552.4096036	test: 567.9853489	best: 567.9853489 (180)	total: 1.22s	remaining: 2.15s
181:	learn: 551.9256147	test: 567.5175314	best: 567.5175314 (181)	total: 1.23s	remaining: 2.14s
182:	learn: 551.4131621	test: 567.1387120	best: 567.1387120 (182)	total: 1.23s	remaining: 2.14s
183:	learn: 550.7070161	test: 566.9438012	best: 566.9438012 (183)	total: 1.24s	remaining: 2.13s
184:	learn: 550.2860345	test: 566.7379192	best: 566.7379192 (184)	total: 1.25s	remaining: 2.12s
185:	learn: 549.7582644	test: 566.1617541

269:	learn: 516.9497421	test: 550.3420113	best: 550.3420113 (269)	total: 1.83s	remaining: 1.55s
270:	learn: 516.6541653	test: 550.1092467	best: 550.1092467 (270)	total: 1.83s	remaining: 1.55s
271:	learn: 516.4615622	test: 549.9544141	best: 549.9544141 (271)	total: 1.84s	remaining: 1.54s
272:	learn: 516.3296581	test: 549.8208789	best: 549.8208789 (272)	total: 1.85s	remaining: 1.54s
273:	learn: 516.0649506	test: 549.8212178	best: 549.8208789 (272)	total: 1.85s	remaining: 1.53s
274:	learn: 515.8792954	test: 549.6375918	best: 549.6375918 (274)	total: 1.86s	remaining: 1.52s
275:	learn: 515.1930446	test: 549.8121354	best: 549.6375918 (274)	total: 1.87s	remaining: 1.52s
276:	learn: 514.9728426	test: 549.6499910	best: 549.6375918 (274)	total: 1.88s	remaining: 1.51s
277:	learn: 514.5911735	test: 549.5598576	best: 549.5598576 (277)	total: 1.88s	remaining: 1.5s
278:	learn: 514.2969331	test: 549.4911767	best: 549.4911767 (278)	total: 1.89s	remaining: 1.5s
279:	learn: 514.1216813	test: 549.3033759	

358:	learn: 491.1803147	test: 545.3534786	best: 545.3534786 (358)	total: 2.45s	remaining: 962ms
359:	learn: 491.0518060	test: 545.3226808	best: 545.3226808 (359)	total: 2.46s	remaining: 955ms
360:	learn: 490.7238358	test: 545.2683088	best: 545.2683088 (360)	total: 2.46s	remaining: 949ms
361:	learn: 490.5173295	test: 545.1414735	best: 545.1414735 (361)	total: 2.47s	remaining: 943ms
362:	learn: 490.4232628	test: 545.0681356	best: 545.0681356 (362)	total: 2.48s	remaining: 937ms
363:	learn: 490.2969023	test: 545.0184920	best: 545.0184920 (363)	total: 2.49s	remaining: 930ms
364:	learn: 490.0555527	test: 545.0489441	best: 545.0184920 (363)	total: 2.5s	remaining: 923ms
365:	learn: 489.5435243	test: 545.0353670	best: 545.0184920 (363)	total: 2.5s	remaining: 917ms
366:	learn: 489.2232972	test: 544.9700036	best: 544.9700036 (366)	total: 2.51s	remaining: 910ms
367:	learn: 488.7978238	test: 544.9025978	best: 544.9025978 (367)	total: 2.52s	remaining: 903ms
368:	learn: 488.3448373	test: 544.9635034	

446:	learn: 468.9836331	test: 544.3334185	best: 544.0726844 (439)	total: 3.06s	remaining: 363ms
447:	learn: 468.6898070	test: 544.3296042	best: 544.0726844 (439)	total: 3.06s	remaining: 356ms
448:	learn: 468.5331513	test: 544.2454845	best: 544.0726844 (439)	total: 3.07s	remaining: 349ms
449:	learn: 468.3382950	test: 544.2049482	best: 544.0726844 (439)	total: 3.08s	remaining: 343ms
450:	learn: 468.1020082	test: 544.0864098	best: 544.0726844 (439)	total: 3.09s	remaining: 336ms
451:	learn: 467.6570534	test: 543.9514562	best: 543.9514562 (451)	total: 3.1s	remaining: 329ms
452:	learn: 467.3873703	test: 543.9016472	best: 543.9016472 (452)	total: 3.1s	remaining: 322ms
453:	learn: 467.3173710	test: 543.9022951	best: 543.9016472 (452)	total: 3.11s	remaining: 315ms
454:	learn: 467.0733572	test: 543.9057236	best: 543.9016472 (452)	total: 3.12s	remaining: 308ms
455:	learn: 466.6526040	test: 543.7115513	best: 543.7115513 (455)	total: 3.12s	remaining: 302ms
456:	learn: 466.2247340	test: 543.6490059	

{'params': {'depth': 8,
  'iterations': 500,
  'learning_rate': 0.03,
  'l2_leaf_reg': 0.2},
 'cv_results': defaultdict(list,
             {'iterations': [0,
               1,
               2,
               3,
               4,
               5,
               6,
               7,
               8,
               9,
               10,
               11,
               12,
               13,
               14,
               15,
               16,
               17,
               18,
               19,
               20,
               21,
               22,
               23,
               24,
               25,
               26,
               27,
               28,
               29,
               30,
               31,
               32,
               33,
               34,
               35,
               36,
               37,
               38,
               39,
               40,
               41,
               42,
               43,
               44,
               

# Predict model

In [59]:
# rf model predict
y_pred = model.predict(X_test)

# RMSE calculation

In [60]:
# RMSE calculation
rmse = mean_squared_error(y_test, y_pred, squared=False)
rmse

533.892819525681

# Model train 100 %

In [29]:
"""
train_dataset_100 = cb.Pool(X)
"""

In [23]:
"""
model = cb.CatBoostRegressor(loss_function='RMSE')
"""

In [37]:
"""
# rf model train
grid_b = {'iterations': [100, 150, 500],
        'learning_rate': [0.03, 0.1, 0.3],
        'depth': [2, 4, 6, 8],
        'l2_leaf_reg': [0.2, 0.5, 1, 3]}
model.grid_search(grid_b, train_dataset_100)
"""

"\n# rf model train\ngrid_b = {'iterations': [100, 150, 500],\n        'learning_rate': [0.03, 0.1, 0.3],\n        'depth': [2, 4, 6, 8],\n        'l2_leaf_reg': [0.2, 0.5, 1, 3]}\nmodel.grid_search(grid_b, train_dataset_100)\n"

# Read diamonds_test_processed

In [61]:
# Read diamonds_test_processed
diamonds_test_basic = pd.read_csv('../data/diamonds_test_processed.csv')
diamonds_test_basic.head()

carat  cut  color  clarity  depth  table     x     y     z
0   0.79    3      2        2   62.7   60.0  5.82  5.89  3.67
1   1.20    0      6        4   61.0   57.0  6.81  6.89  4.18
2   1.57    4      4        2   62.2   61.0  7.38  7.32  4.57
3   0.90    3      2        2   63.8   54.0  6.09  6.13  3.90
4   0.50    3      2        4   62.9   58.0  5.05  5.09  3.19

# Feature engineering

In [62]:
diamonds_test_basic['table_xy'] = (diamonds_test_basic['table'].mean()*(diamonds_test_basic['x']*diamonds_test_basic['y']).mean()-diamonds_test_basic['table']*(diamonds_test_basic['x']*diamonds_test_basic['y']))
diamonds_test_basic['depth_z'] = (diamonds_test_basic['depth'].mean()*diamonds_test_basic['z'].mean()-diamonds_test_basic['depth']*diamonds_test_basic['z'])
diamonds_test_basic['volume'] = diamonds_test_basic['x']*diamonds_test_basic['y']*diamonds_test_basic['z']
diamonds_test_basic['super_feature'] = diamonds_test_basic['carat'] / diamonds_test_basic['table'] * diamonds_test_basic['depth']
diamonds_test_basic.head()

carat  cut  color  clarity  depth  table     x     y     z    table_xy  \
0   0.79    3      2        2   62.7   60.0  5.82  5.89  3.67   -93.26473   
1   1.20    0      6        4   61.0   57.0  6.81  6.89  4.18  -710.96803   
2   1.57    4      4        2   62.2   61.0  7.38  7.32  4.57 -1331.79433   
3   0.90    3      2        2   63.8   54.0  6.09  6.13  3.90   -52.38853   
4   0.50    3      2        4   62.9   58.0  5.05  5.09  3.19   472.66227   

     depth_z      volume  super_feature  
0 -11.338107  125.806866       0.825550  
1 -36.209107  196.129362       1.284211  
2 -65.483107  246.878712       1.600885  
3 -30.049107  145.593630       1.063333  
4  18.119893   81.997355       0.542241

# Predict diamonds_test_basic

In [63]:
# Define fearures
X_dtfe_2 = diamonds_test_basic[['carat', 
                           'cut',
                           'color', 
                           'clarity',
                           'table_xy', 
                           'depth_z',
                          'volume']]

In [47]:
# predict
y_predfe_2 = model.predict(X_dtfe_2).clip(0, 30000)
y_predfe_2 

array([2953.45816449, 5552.02351086, 9662.82912368, ..., 3117.60574606,
       2117.18455721,  754.83746979])

# Create sample_submission

In [49]:
predictions_fe_2 = pd.DataFrame(y_predfe_2).rename(columns = {0:'price'})
predictions_fe_2.index.names = ['id']
predictions_fe_2

price
id                
0      2953.458164
1      5552.023511
2      9662.829124
3      3843.793842
4      1649.883189
...            ...
13480  1681.583765
13481  2281.964617
13482  3117.605746
13483  2117.184557
13484   754.837470

[13485 rows x 1 columns]

In [50]:
predictions_fe_2.to_csv('../predictions/predictions_catboost.csv')